In [60]:
import astropy.units as units
import astropy.constants as constants
import matplotlib.pyplot as plt
import sympy as sym
import numpy as np 
import pandas as pd
import plotly.express as px
import plotly.figure_factory as ff
import requests
import re
import os
a, b, c, d, e, f, g, h, i, j, k, l, m = sym.symbols('a b c d e f g h i j k l m')
n, o, p, q, r, s, t, u, v, w, x, y, z = sym.symbols('n o p q r s t u v w x y z')
symbol_list = (a, b, c, d, e, f, g, h, i, j, k, l, m, n, o, p, q, r, s, t, u, v,
w, x, y, z)
A, B, C, D, E, F, G, H, I, J, K, L, M = sym.symbols('A B C D E F G H I J K L M')
N, O, P, Q, R, S, T, U, V, W, X, Y, Z = sym.symbols('N O P Q R S T U V W X Y Z')
symbol_list = (A, B, C, D, E, F, G, H, I, J, K, L, M, N, O, P, Q, R, S, T, U, 
               V, W, X, Y, Z)
#%matplotlib notebook #incompatible with mpmath

#TODO: 

-Write a function that plots half life vs power density with optional inputs including:
half life units, minimum half life, minimum power density, decay types.

-Simulate how easily different nuclides can be produced.

#Import half-lifes and energy per emission from databases
[Zotero Collection](https://www.zotero.org/groups/4549380/batteries/collections/59RQX9TX) / [Atomic Mass Data Center (AMDC)](https://www-nds.iaea.org/amdc/)



In [61]:
(units.yottasecond).to(units.year)

3.1688087814028948e+16

##Nubase2020


In [62]:
url = "https://www-nds.iaea.org/amdc/ame2020/nubase_3.mas20.txt"
response = requests.get(url)
nubase = np.array(response.text.split('\n'))
nubase = nubase[25:]
column_dict = {'AAA': np.arange(1,4), 'ZZZi':np.arange(5,9),
'A El': np.arange(11,17), 's': np.array([17]), 
'Mass #': np.arange(19,32), 'dMass #': np.arange(32,43),
'Exc #': np.arange(43,55), 'dE #': np.arange(55,66),
'Orig': np.arange(66,68), 'Isom.Unc': np.array([68]),
'Isom.Inv': np.array([69]), 'T #': np.arange(70, 79),
'unit T': np.arange(78, 81), 'dT': np.arange(81, 89),
'Jpi */#/T=': np.arange(88, 103), 
'Ensdf year': np.arange(102, 105), 
'Discovery': np.arange(114, 119), 'BR': np.arange(119, 210)}
#make an array of lists of the columns

def clean(array):
    #turn the array of characters into a string and remove spaces
    array = ''.join(array).replace(' ', '')
    try:
        array = array.astype(float)
    except:
        pass
    return array

#Turn the list of strings into a multidimensional array

In [63]:
#get substring from each item in array
def get_substring(array, start, end):
    #start and end are the indices of the substring
    #returns a list of the substring
    try:
        return [item[start:end] for item in array]
    except:
        print(len(item), end)
        return ("error")

def make_dict_from_string_array(column_dict, string_array):
    #column_dict is a dictionary of the column names and the indices
    #string_array is a list of strings
    #returns a dictionary of the column names and the values
    nubase_dict = {}
    for key, columns in column_dict.items():
        nubase_dict[key] = get_substring(string_array, columns[0], columns[-1])
    return nubase_dict

nubase_df = pd.DataFrame(make_dict_from_string_array(column_dict, nubase))
nubase_df

AAA ZZZi   A El s         Mass #     dMass #        Exc #        dE #  \
0     01  000  1n         8071.3181      0.0004                              
1     01  010  1H         7288.971064    0.000013                            
2     02  010  2H        13135.722895    0.000015                            
3     03  010  3H        14949.81090     0.00008                             
4     03  020  3He       14931.21888     0.00006                             
...   ..  ...    ... ..           ...         ...          ...         ...   
5839  93  180  293Og     98800#        710#                                  
5840  94  170  294Ts     96400#        590#                                  
5841  94  180  294Og     99320#        550#                                  
5842  95  180  295Og     01370#        660#                                  
5843                                                                         

     Orig Isom.Unc Isom.Inv       T # unit T       dT      Jpi */#/T=  \
0                            609.8         s  0.6      1/2+*            
1                            stbl                      1/2+*            
2                            stbl                      1+*              
3                             12.32        y  0.02     1/2+*            
4                            stbl                      1/2+*            
...   ...      ...      ...       ...    ...      ...             ...   
5839    N                      1#         ms                            
5840                          70          ms  30                        
5841                            0.7       ms  0.3      0+               
5842                          680         ms  540                       
5843                                                                    

     Ensdf year Discovery             BR  
0            06      1932         B-=100  
1            06      1920  IS=99.9855 78  
2            03      1932   IS=0.0145 78  
3            00      1934         B-=100  
4            98      1934    IS=0.0002 2  
...         ...       ...            ...  
5839         00      2010            A ?  
5840         19      2010          A=100  
5841         05      2004    A~100; SF ?  
5842                 2006          A~100  
5843                                      

[5844 rows x 18 columns]

In [64]:
nubase_df.to_csv('nubase_df.csv')
        

##AME2020

In [65]:
url = "https://www-nds.iaea.org/amdc/ame2020/mass_1.mas20.txt"
response = requests.get(url)
Atomic_mass_table_2020 = response.text
#Now we want to convert a string to a pandas dataframe
Atomic_mass_table_2020 = list(Atomic_mass_table_2020.split('\n'))
split_table = Atomic_mass_table_2020[36:]

def clean_uncertainty(uncertainty):
    uncertainty = uncertainty.replace('.', '')
    uncertainty = uncertainty.replace('a', '0')
    uncertainty = uncertainty.replace('#', '')
    uncertainty = float("0." + uncertainty)
    return uncertainty

def clean_row(row):
    while True:
        try:
            row[2] = int(row[2])
            number = row.pop(0)
        except:
            row.insert(0, number)
            break
    #The above while loop ensures the first column is the number of neutrons
    try: 
        row[4] = float(row[4]) #if this fails, we the row is valid
        row.insert(4, "NA")
    except:
        pass
    try:
        row[10] = row[10].replace('#', '')
        row[10] = float(row[10]) #This means element 9 is *
    except:
        row.insert(11, "NA")
    #if not (len(row) == 15):
    #    print(row, len(row), row[9])
    #print(len(row), row)
    row[12] = float(row[12]) + clean_uncertainty(row[13])
    #this number was formatted weirdly, so we need to clean it up
    row.pop(13)
    
    return row

for i in range(len(split_table)):
    try:
        split_table[i] = clean_row(split_table[i].split())
    except:
        print(split_table[i].split())
#We know the column names are on row 34 (0-indexed)
#now we will make a pandas dataframe from the list of rows
#Annoyingly, the column names don't include the uncertainties, so we need to add them
my_column_names = ["N", "Z", "A", "Elt.", "Orig.", "Mass excess (keV)", "Mass excess (uncertainty)",
 "Binding energy per nucleon (keV)", "Binding energy per nucleon (uncertainty)", 
 "Beta-decay Type", "Beta-decay energy (keV)", 
 "Beta-decay energy (uncertainty)", "Atomic mass (μu)", 
 "Atomic mass (uncertainty)"]
Atomic_mass_table_2020 = pd.DataFrame(split_table, columns = my_column_names)

[]


In [66]:
Atomic_mass_table_2020

N      Z      A  Elt. Orig. Mass excess (keV)  \
0        1    0.0    1.0     n    NA        8071.31806   
1        0    1.0    1.0     H    NA       7288.971064   
2        1    1.0    2.0     H    NA      13135.722895   
3        2    1.0    3.0     H    NA        14949.8109   
4        1    2.0    3.0    He    NA       14931.21888   
...    ...    ...    ...   ...   ...               ...   
3554   175  118.0  293.0    Og    -a           198802#   
3555   177  117.0  294.0    Ts    -a           196397#   
3556   176  118.0  294.0    Og    -a           199320#   
3557   177  118.0  295.0    Og    -a           201369#   
3558  None    NaN    NaN  None  None              None   

     Mass excess (uncertainty) Binding energy per nucleon (keV)  \
0                      0.00044                              0.0   
1                     0.000013                              0.0   
2                     0.000015                        1112.2831   
3                      0.00008                        2827.2654   
4                      0.00006                       2572.68044   
...                        ...                              ...   
3554                      709#                            7078#   
3555                      593#                            7092#   
3556                      553#                            7079#   
3557                      655#                            7076#   
3558                      None                             None   

     Binding energy per nucleon (uncertainty) Beta-decay Type  \
0                                         0.0              B-   
1                                         0.0              B-   
2                                      0.0002              B-   
3                                      0.0003              B-   
4                                     0.00015              B-   
...                                       ...             ...   
3554                                       2#              B-   
3555                                       2#              B-   
3556                                       2#              B-   
3557                                       2#              B-   
3558                                     None            None   

     Beta-decay energy (keV) Beta-decay energy (uncertainty)  \
0                    782.347                          0.0004   
1                          *                              NA   
2                          *                              NA   
3                   18.59202                         0.00006   
4                   -13736.0                           2000#   
...                      ...                             ...   
3554                       *                              NA   
3555                 -2923.0                            811#   
3556                       *                              NA   
3557                       *                              NA   
3558                    None                            None   

      Atomic mass (μu) Atomic mass (uncertainty)  
0             1.008665                   0.00047  
1             1.007825                  0.000014  
2             2.014102                  0.000015  
3             3.016049                   0.00008  
4             3.016029                   0.00006  
...                ...                       ...  
3554        293.213423                      761#  
3555        294.210840                      637#  
3556        294.213979                      594#  
3557        295.216178                      703#  
3558               NaN                      None  

[3559 rows x 14 columns]

In [67]:
#Now we want to write the dataframe to a csv file
Atomic_mass_table_2020.to_csv("Atomic_mass_table_2020.csv")

##Half-life vs. Beta Emission

In [68]:
AM_table = Atomic_mass_table_2020
'''
First we will convert the atomic mass numbers to integers then concatenate them
with their chemical symbol. 
'''
def concat_add_space(a, b):
  try: 
    a = int(a)
  except:
    a = 0
  return (str(a) + " " + str(b))


AM_table['A Elt.'] = [concat_add_space(A, AM_table['Elt.'][row]) for row, A 
                 in enumerate(AM_table['A'])]

In [69]:
chemical_symbols = AM_table['A Elt.']

units_dict = {'s': units.s, 'h': units.h, 'd': units.d, 'm' : units.minute, 
              'y': units.year, 'ky': units.kiloyear, 'My': units.megayear,
              'as': units.attosecond, 'ys': units.yoctosecond, 'zs': units.zeptosecond,
              'ms': units.ms, 'ns': units.ns, 'us': units.us, 'μs': units.microsecond,
              'ps': units.ps, 'fs': units.fs, 'My': units.myr, 'Gy': units.gigayear,
              'ty': units.Tyr, 'py': units.Pyr, 'ny': units.nanoyear, 'Yy': units.yottayear,
              'Zy': units.zettayear, 'Ey': units.Eyr,}

def convert_half_life(number, unit, units_dict):
  try: 
    half_life = float(number) * units_dict[unit].to(units.year)
  except: #isotope is stable
    half_life = 'unknown'
  return half_life

def remove_symbols(string, symbol_list):
  for symbol in symbol_list:
    string = string.replace(symbol, "")
  return string

sym_list = [" ", "#", "*"]

half_lives_seconds = [convert_half_life(remove_symbols(t, sym_list), 
                    remove_symbols(nubase_df['unit T'][row], sym_list), 
                    units_dict) for row, t in enumerate(nubase_df['T #'])]
nubase_df['T in s'] = half_lives_seconds

In [70]:
#Now we will find which nuclides are in both datasets
AM_table['A Elt.'] = [symbol.replace(" ","") for symbol in AM_table['A Elt.']]
AM_table['A Elt.']
#overlapping_nuclid

0          1n
1          1H
2          2H
3          3H
4         3He
        ...  
3554    293Og
3555    294Ts
3556    294Og
3557    295Og
3558    0None
Name: A Elt., Length: 3559, dtype: object

In [71]:
#Now we will find which nuclides are in both datasets
nubase_df['A El'] = [symbol.replace(" ","") for symbol in nubase_df['A El']]
nubase_df['A El']
#overlapping_nuclid

0          1n
1          1H
2          2H
3          3H
4         3He
        ...  
5839    293Og
5840    294Ts
5841    294Og
5842    295Og
5843         
Name: A El, Length: 5844, dtype: object

In [72]:
nuclide_list = np.array([nuclide.lower() for nuclide in nubase_df['A El']])
np.savetxt("nuclide_list.csv", nuclide_list, delimiter=",", fmt="%s")

In [73]:
intersection = set(nubase_df['A El']) & set(AM_table['A Elt.'])
intersection
#the nuclides in nubase are a subset of those in AM

{'25Na',
 '184Lu',
 '72Ga',
 '165Lu',
 '218Po',
 '21C',
 '216Pa',
 '187Re',
 '59Fe',
 '109Sn',
 '262Md',
 '161W',
 '138Nd',
 '171Dy',
 '226Pa',
 '172Os',
 '85Y',
 '274Bh',
 '226Pu',
 '91Ru',
 '285Rg',
 '77Ni',
 '116Rh',
 '146Cs',
 '234Am',
 '43Ti',
 '56Ga',
 '76Br',
 '206Fr',
 '287Mc',
 '45Cr',
 '227Po',
 '41Ti',
 '243Cm',
 '153Tm',
 '124La',
 '229Rn',
 '222Pa',
 '160Re',
 '170Eu',
 '41Ar',
 '113I',
 '77Ga',
 '163Tm',
 '229Np',
 '72As',
 '231Rn',
 '47P',
 '65Br',
 '130Pr',
 '206Hg',
 '227Fr',
 '73Ni',
 '62Ni',
 '188Hg',
 '63Sc',
 '171Tm',
 '96Kr',
 '97Kr',
 '276Cn',
 '75Br',
 '110Te',
 '25Ne',
 '115Nb',
 '84Ge',
 '141Pm',
 '218Pa',
 '111Pd',
 '74Zn',
 '226Po',
 '290Fl',
 '214Fr',
 '165Dy',
 '278Mt',
 '123Rh',
 '198Pt',
 '281Ds',
 '20O',
 '81Sr',
 '115Ba',
 '57Ti',
 '150Eu',
 '120Ba',
 '184Au',
 '48Ar',
 '130I',
 '46S',
 '166Tm',
 '221Fr',
 '100Pd',
 '179Hf',
 '113Ba',
 '164Er',
 '90Rb',
 '114Sn',
 '62Co',
 '161Tb',
 '175Re',
 '29S',
 '107Sn',
 '165Gd',
 '247Es',
 '14F',
 '260Lr',
 '49N

In [74]:
#Now we want the beta decay energy for every nuclide in nubase
AM_table['Beta-decay energy (keV)']

0        782.347
1              *
2              *
3       18.59202
4       -13736.0
          ...   
3554           *
3555     -2923.0
3556           *
3557           *
3558        None
Name: Beta-decay energy (keV), Length: 3559, dtype: object

In [75]:
a = [x for x in np.where(np.arange(10) == 5)]
a

[array([5], dtype=int64)]

In [76]:
AM_symbols = list(AM_table['A Elt.'])
nubase_symbols = list(nubase_df['A El'])

In [77]:
AM_rows = [AM_symbols.index(n) for n in
intersection]
nubase_rows = [nubase_symbols.index(n) for
n in intersection]

In [78]:
e_t_dict = {}
e_t_dict['Beta-decay energy (keV)'] = list(
AM_table['Beta-decay energy (keV)'][AM_rows])
e_t_dict['Half life (years)'] = list(nubase_df['T in s'][nubase_rows])
e_t_dict['Isotope'] = list(list(intersection))

In [79]:
px.scatter(y = e_t_dict['Beta-decay energy (keV)'],
x = e_t_dict['Half life (years)'], 
hover_name = e_t_dict['Isotope'],
labels = {'y': 'Beta-decay energy (keV)',
'x': 'Half life (years)'}, log_x = True)

###Retrieving data from dataframes and dictionaries

In [80]:
nubase_isotopes = list(nubase_df['A El'])
nubase_br_list = list(nubase_df['BR'])

#Calculations for Power vs. Half-life

In [81]:

def half_life_to_energy(half_life, time, initial_mass, decay_energy, 
                        molar_mass):
    '''
    decay_energy is in keV. All other units are acceptable as long as they are
    consistent with the units of time and initial_mass.
    '''
    initial_counts = initial_mass * 6.0221408 * (10**23) / molar_mass 
    decay_count = initial_counts * (1 - (.5 ** (time / half_life)))
    try:
      energy = (decay_energy * decay_count / (2)).to(units.J) 
    except:
      energy = (decay_energy * decay_count * units.keV / 2).to(units.J) 
    #power emitted after one half life to be conservative
    return energy #joules, counts


half_life_U_238 = 1.41*(10 ** 17) #seconds 
half_life_CA_48 = 6.4 * (10 ** 26.5) #seconds
#around 10^9.5 years :)
half_life = (10 ** 11) * units.s
mass = 1 * units.g
time = 1 * units.s
decay_energy = 66 * units.keV
molar_mass = 63 * units.g
power = (half_life_to_energy(half_life, time, mass, decay_energy,                             
            molar_mass) / (time)).to(units.W)
print(mass, "generates", power, "\nHalf of the energy" +
      " will be lost in", (time).to(units.year))

1.0 g generates 0.00035031531424445367 W 
Half of the energy will be lost in 3.168808781402895e-08 yr


In [82]:
'''
Here we will plot half-life versus power generated in first second of existence.
Based on the plot this makes, since there are about 10^9.5 seconds in a century,
the ideal half life is around 10^10 seconds. This will mean after a century,
it will only half of the remaining mass (and thus presumably only produce half
of the energy indicated in this plot). 

def calc_half_power(min_half_life, max_half_life, steps, mass, molar_mass):
  precise_half_lives, power_array = [], []
  time = 1
  for exponent in np.linspace(min_half_life, max_half_life, steps):
        half_life = 10 ** exponent
        precise_half_lives.append(half_life)
        power = half_life_to_energy(half_life, time, mass, dec, 
                                    molar_mass)
        power_array.append(power)
  return (precise_half_lives, power_array)

def plot_power_vs_half_life(min_half_life, max_half_life, steps, mass, 
                            molar_mass, point_size, provide_fit, dpi):
  
  #Note that the half-lifes give are assumed to be a power of 10
  
  precise_half_lives, power_array = calc_half_power(min_half_life, 
                                      max_half_life, steps, mass, molar_mass)
  plt.figure(dpi = dpi)
  plt.scatter(x = precise_half_lives, y= power_array, s = point_size)
  plt.xscale("log"), plt.yscale("log")
  plt.title("β- Decay of " + str(mass * units.g) + " of Different Isotopes")
  plt.ylabel("Power in Watts")
  plt.xlabel("Half Life in Seconds")
  plt.grid(which='major', color='black')
  plt.grid(which='minor', color='grey', alpha=0.4)
  plt.minorticks_on()
  logX, logY = np.log10(precise_half_lives), np.log10(power_array)
  plt.show()
  if provide_fit:
    return np.polyfit(logX, logY, 1)
plot_power_vs_half_life(0, 15, 100, 1, 118, point_size = 20, 
                        provide_fit = False, dpi = 1000)
'''



'\nHere we will plot half-life versus power generated in first second of existence.\nBased on the plot this makes, since there are about 10^9.5 seconds in a century,\nthe ideal half life is around 10^10 seconds. This will mean after a century,\nit will only half of the remaining mass (and thus presumably only produce half\nof the energy indicated in this plot). \n\ndef calc_half_power(min_half_life, max_half_life, steps, mass, molar_mass):\n  precise_half_lives, power_array = [], []\n  time = 1\n  for exponent in np.linspace(min_half_life, max_half_life, steps):\n        half_life = 10 ** exponent\n        precise_half_lives.append(half_life)\n        power = half_life_to_energy(half_life, time, mass, dec, \n                                    molar_mass)\n        power_array.append(power)\n  return (precise_half_lives, power_array)\n\ndef plot_power_vs_half_life(min_half_life, max_half_life, steps, mass, \n                            molar_mass, point_size, provide_fit, dpi):\n  \n  #

In [83]:
'''
Interestingly, zooming in we have a half-life of 10^9 seconds (30 years) 
corresponds to about 1 W/g. 
Conveniently, on this log-log graph, the slope is also about -1. 
plot_power_vs_half_life(3, 7, 500, 1, 63, 2, provide_fit = True, dpi = 10**3)
'''

'\nInterestingly, zooming in we have a half-life of 10^9 seconds (30 years) \ncorresponds to about 1 W/g. \nConveniently, on this log-log graph, the slope is also about -1. \nplot_power_vs_half_life(3, 7, 500, 1, 63, 2, provide_fit = True, dpi = 10**3)\n'

In [84]:
half_life_Si_31 = (157 * units.minute).to(units.s)
power_Si_31_per_gram = (half_life_to_energy(half_life_Si_31, time, 1, 
                      68 * units.keV, 31) / time).to(units.W)
power_Si_31_per_gram

<Quantity 7786.40702737 W>

In [85]:
half_life_Ni_63 = (100.1 * units.year).to(units.s)
power_Ni_63_per_gram = (half_life_to_energy(half_life_Ni_63, time, 1, 17 * units.keV, 
                                  63) / time).to(units.W)
power_Ni_63_per_gram #200kg could power a car for 50 years :) 

<Quantity 0.00285645 W>

#Power and energy density for each isotope
We will use the above functions and dataframes to calculate the energy and power density of each isotope. We will only use the energy from beta decay for our calculations.
This generates a dictionary where each isotope is a key, and each value includes every measured decay type label, abundance (in percent), and uncertainty (also in percent).

##Evaluating all isotopes with a half life and decay energy in e_t_dict

In [86]:
all_decay_types = pd.DataFrame(e_t_dict)
#drop the isotopes that are missing half life or beta-decay energy
no_energy = [row for row, energy in enumerate(all_decay_types['Beta-decay energy (keV)']) 
            if type(energy ) is str]
no_half_life = [row for row, half_life in enumerate(all_decay_types['Half life (years)']) 
               if type(half_life) is str]
all_types_unmeasured_rows = no_energy + no_half_life
all_decay_types['Half life (seconds)'] = [
float(t * units.year.to(units.s)) 
if not type(t) is str else 'unknown'
for t in all_decay_types['Half life (years)']]
all_types_measured_rows = [row for row in range(all_decay_types.shape[0])
if not row in all_types_unmeasured_rows]
all_decay_types = all_decay_types.iloc[all_types_measured_rows, :].reset_index()

In [87]:
all_decay_types

index Beta-decay energy (keV) Half life (years) Isotope  \
0         0               3834.9684          0.000002    25Na   
1         1                  5199.0          0.000001   184Lu   
2         2               3997.6263            0.0016    72Ga   
3         3               -4806.735           0.00002   165Lu   
4         4                256.4334          0.000006   218Po   
...     ...                     ...               ...     ...   
2944   3553               1645.6311          0.000005   108Ag   
2945   3554                   687.0            10.728    85Kr   
2946   3555                 44.7559            21.772   227Ac   
2947   3556                 -8470.0          0.000028   140Sm   
2948   3557               6204.9921               0.0   107Mo   

     Half life (seconds)  
0                   59.1  
1                   20.0  
2                50490.0  
3                  644.4  
4                 185.82  
...                  ...  
2944              142.92  
2945         338549932.8  
2946         687072067.2  
2947               889.2  
2948                 3.5  

[2949 rows x 5 columns]

In [88]:
def get_isotope_info(isotope, info = None, isotope_column = None,
    dataset = {}, isotope_list = None, list_to_search = []):                  
  '''
  isotope_list and list_to_search are optional arguments.
  If list_to_search is not provided, then info must be provided.
  If isotope_list is not provided, then dataset and isotope_column
  must be provided.
  '''
  if isotope_list is None:
    isotope_list = list(dataset[isotope_column])
  row = 0
  try:
    row = isotope_list.index(isotope)
  except:
    print("error for isotope: ", isotope)
  if len(list_to_search) == 0:
    try:
      list_to_search = list(dataset[info])
    except:
      print("info to search for not entered")
      return
  return list_to_search[row]


def power_density_of_isotope(isotope, isotope_data_frame = None, 
                             half_life_column = None, 
                             decay_energy_column = None, isotope_list = [],
                             decay_energy_list = [], half_life_list = []):
    molar_mass = float(re.sub(r'[^\d.]', '', isotope))
    if(len(isotope_list) == 0):
      isotope_list = isotope_data_frame['Isotope']
    isotope_list = list(isotope_list)
    if(len(decay_energy_list) == 0):
      decay_energy_list = list(isotope_data_frame[decay_energy_column])
    if(len(half_life_list) == 0):
      half_life_list = list(isotope_data_frame[half_life_column])
    row = isotope_list.index(isotope)
    half_life, decay_energy = half_life_list[row], decay_energy_list[row]
    power = (half_life_to_energy(half_life, 1, 1, decay_energy * units.keV, 
                                molar_mass) / units.J)
    return power 
    #power density is in units of W/g

In [89]:
all_decay_types_isotopes = list(all_decay_types['Isotope'])
all_decay_types_half_lives_s = list(all_decay_types['Half life (seconds)'])
all_decay_types_half_lives_y = list(all_decay_types['Half life (years)'])
all_decay_types_decay_energies = list(all_decay_types['Beta-decay energy (keV)'])
power_densities = [float(power_density_of_isotope(n, isotope_list=all_decay_types_isotopes,
decay_energy_list=all_decay_types_decay_energies, half_life_list=all_decay_types_half_lives_s)) 
                    for n in all_decay_types_isotopes]

In [90]:
all_decay_types['Power density (W/g)'] = power_densities
all_decay_types

index Beta-decay energy (keV) Half life (years) Isotope  \
0         0               3834.9684          0.000002    25Na   
1         1                  5199.0          0.000001   184Lu   
2         2               3997.6263            0.0016    72Ga   
3         3               -4806.735           0.00002   165Lu   
4         4                256.4334          0.000006   218Po   
...     ...                     ...               ...     ...   
2944   3553               1645.6311          0.000005   108Ag   
2945   3554                   687.0            10.728    85Kr   
2946   3555                 44.7559            21.772   227Ac   
2947   3556                 -8470.0          0.000028   140Sm   
2948   3557               6204.9921               0.0   107Mo   

     Half life (seconds)  Power density (W/g)  
0                   59.1         8.628728e+07  
1                   20.0         4.643279e+07  
2                50490.0         3.677207e+04  
3                  644.4        -1.510894e+06  
4                 185.82         2.112869e+05  
...                  ...                  ...  
2944              142.92         3.556475e+06  
2945         338549932.8         7.983105e-01  
2946         687072067.2         9.595749e-03  
2947               889.2        -2.274277e+06  
2948                 3.5         5.026334e+08  

[2949 rows x 6 columns]

#Evaluation of Prospective Isotopes for batteries
We first define the following
*   If $a > b$, then $max(a,b) = a$ and $min(a,b) = b$. 
*   $\rho_{p}$ is the energy in watts produced by 1g of the nuclide after 1 half life
*   $t_{\frac{1}{2}}$ is the half life in years
*   $f$ is the fraction of decays that are $\beta_{-}$ decay (one neutron emitting a W$^{-}$ boson which then decays to an up quark, an electron, and an electron neutrino). Future analysis will simulate only the electron spectra to better characterize the power produced by the battery. 

We define
\begin{equation}
\begin{split}
t = min(t_{\frac{1}{2}}, 100) \\
k = min(t, \rho_{p})^7 \\
E = max(0, kt\rho_{p})\\
\end{split}
\end{equation}
where a higher value for $E$ is used to distinguish which isotopes would make ideal batteries, and lower values are incredibly dangerous, produce insufficient power, and/or decay too quickly. Isotopes with a half life less than one year were not considered. 




In [91]:
def evaluate_isotope_all_decay_types(half_life, power_density):
    evaluation = 0
    try:
        half_life = half_life / 100
        #half_life = min(half_life, 1000)
        coeff = min(half_life, power_density) ** 10
        if coeff > 0:
            evaluation = max(0, (coeff * half_life * power_density))
    except: 
        return 0
    return evaluation
evaluations_all_decay_types = np.array([evaluate_isotope_all_decay_types(h, p) for 
                                h, p in zip(all_decay_types_half_lives_y, power_densities)])
#normalize the evaluations to use for the color scale
evaluations_all_decay_types = evaluations_all_decay_types / np.max(evaluations_all_decay_types)
all_decay_types['Evaluation'] = evaluations_all_decay_types
all_decay_types = all_decay_types.sort_values(by = 'Evaluation', ascending = False)
evaluations_all_decay_types = list(all_decay_types['Evaluation'])
all_decay_types

index Beta-decay energy (keV) Half life (years) Isotope  \
958    1167                599.3527              32.9    42Ar   
1957   2363               1175.6285             30.04   137Cs   
2600   3130                545.9674             28.91    90Sr   
70       81                971.6815              36.9   150Eu   
1977   2392               1818.8037            13.517   152Eu   
...     ...                     ...               ...     ...   
1906   2299                 -2412.0          0.000029   265Db   
1905   2298               -267.4488          0.000461    44Sc   
1078   1313              -4540.3012           0.00001   196Bi   
350     421              -1741.2596               0.0   212Po   
2157   2593                 -9898.0               0.0   135Eu   

     Half life (seconds)  Power density (W/g)  Evaluation  
958         1038245040.0         4.596107e-01    1.000000  
1957         947990304.0         3.026930e-01    0.242190  
2600         912330216.0         2.223458e-01    0.008449  
70          1164475440.0         1.860198e-01    0.001516  
1977         426564079.2         9.380257e-01    0.000115  
...                  ...                  ...         ...  
1906               900.0        -3.380481e+05    0.000000  
1905            14551.56        -1.396770e+04    0.000000  
1078               307.8        -2.513783e+06    0.000000  
350                  0.0        -3.962406e+08    0.000000  
2157                 1.5        -1.308860e+09    0.000000  

[2949 rows x 7 columns]

In [92]:
first_row = 0
for row, eval in enumerate(evaluations_all_decay_types):
    if eval == 0:
        first_row = row
        break
all_decay_types = all_decay_types.iloc[:first_row, :]
evaluations_all_decay_types = 1/(-1 * np.log(evaluations_all_decay_types[:first_row]) + 1)
all_decay_types['Evaluation'] = evaluations_all_decay_types
all_decay_types

index Beta-decay energy (keV) Half life (years) Isotope  \
958    1167                599.3527              32.9    42Ar   
1957   2363               1175.6285             30.04   137Cs   
2600   3130                545.9674             28.91    90Sr   
70       81                971.6815              36.9   150Eu   
1977   2392               1818.8037            13.517   152Eu   
...     ...                     ...               ...     ...   
1729   2087                413.8838               0.0   218Fr   
1466   1772               2003.3657               0.0   216At   
1419   1716                940.5125               0.0   214At   
806     985              15986.3855               0.0     26O   
466     563              22104.0579               0.0     28F   

     Half life (seconds)  Power density (W/g)  Evaluation  
958         1038245040.0         4.596107e-01    1.000000  
1957         947990304.0         3.026930e-01    0.413559  
2600         912330216.0         2.223458e-01    0.173200  
70          1164475440.0         1.860198e-01    0.133479  
1977         426564079.2         9.380257e-01    0.099291  
...                  ...                  ...         ...  
1729              0.0014         9.159109e+07    0.003539  
1466              0.0003         4.474431e+08    0.003357  
1419            0.000001         2.120226e+08    0.002719  
806                  0.0         2.966253e+10    0.002030  
466                  0.0         3.808424e+10    0.001441  

[1449 rows x 7 columns]

In [93]:
x = 'Power density (W/g)'
y = 'Half life (years)'
color = 'Evaluation'
hover_name = 'Isotope'
px.scatter(all_decay_types, x = x, y = y, color = color, hover_name = hover_name,
log_x= True, log_y = True, title = 'All decay types with no minimum half life', 
color_continuous_scale = 'algae')

In [94]:
#There is a new file we can convert to a pandas dataframe that has the average beta decay
#source: https://www.doseinfo-radar.com/RADARDecay.html
#source on Google Drive: https://docs.google.com/spreadsheets/d/1D_mDJWseMenElq68H10CD0cncqnBdhZ6EffqfNk0_XU/edit?usp=sharing
file_path = os.getcwd() + "\\ImportedData\\Radardec4OL.csv"
RADAR_df = pd.read_csv(file_path)
RADAR_df.columns = list(("A", "ELEM", "Z", "Radiation Decay Mode", "Half-Life", 
                    "Half-Life Units", "Rad. Type", "Decay Energy (keV)", "Radiation Intensity (%)"))
RADAR_A = list(RADAR_df['A'])
RADAR_ELEM = list(RADAR_df['ELEM'])

def combine_RADAR(RADAR_A, RADAR_ELEM):
    if len(RADAR_ELEM) > 1:
        RADAR_ELEM = list(RADAR_ELEM)
        RADAR_ELEM[1] = str.lower(RADAR_ELEM[1])
        RADAR_ELEM = ''.join(RADAR_ELEM)
    return str(RADAR_A) + str(RADAR_ELEM)
#converts the isotopes to the same format as the other dataframes


RADAR_df['A ELEM'] = [combine_RADAR(RADAR_A[i], str(RADAR_ELEM[i])) for i in range(RADAR_df.shape[0])]

In [95]:
get_isotope_info('60Co', isotope_list=list(RADAR_df['A ELEM']), list_to_search=list(RADAR_df['Decay Energy (keV)']))

95.77

In [96]:
RADAR_df

A ELEM    Z Radiation Decay Mode Half-Life Half-Life Units Rad. Type  \
0        3    H    1                   B-     12.33               Y        B-   
1       10   BE    4                   B-   1510000               Y        B-   
2       11    C    6                   EC    1223.1               S        B+   
3       11    C    6                   EC    1223.1               S    E-AU-K   
4       11    C    6                   EC    1223.1               S      G-AN   
...    ...  ...  ...                  ...       ...             ...       ...   
46792  255   FM  100                    A     20.07               H   G-X-KA2   
46793  255   FM  100                    A     20.07               H   G-X-KA1   
46794  255   FM  100                    A     20.07               H    G-X-KB   
46795  255   FM  100                    A     20.07               H         G   
46796  255   FM  100                    A     20.07               H         G   

       Decay Energy (keV)  Radiation Intensity (%) A ELEM  
0                    5.69                 100.0000     3H  
1                  202.64                 100.0000   10Be  
2                  385.60                  99.7590    11C  
3                    0.17                   0.2217    11C  
4                  511.00                 199.5200    11C  
...                   ...                      ...    ...  
46792              109.87                   0.0177  255Fm  
46793              115.07                   0.0280  255Fm  
46794              129.00                   0.0135  255Fm  
46795              131.00                   0.0280  255Fm  
46796              204.10                   0.0240  255Fm  

[46797 rows x 10 columns]

In [97]:
#Calculate the average beta particle emission for a given isotope using the Fermi function
def fermi_function(z, a):
    return 1 / (np.exp((z - a) / (z + a)) + 1)
fermi_function(0,1)

0.7310585786300049

In [98]:
#Note that this only includes the isotopes in both AM_table and nubase
RADAR_isotopes = list(RADAR_df['A ELEM'])
RADAR_energies = list(RADAR_df['Decay Energy (keV)'])
average_beta_decay_energy = []
decay_types, beta_decay_fractions, beta_decay_list = {}, {}, []
for n in intersection:
  decay_distr =  re.split(r' |;|=|<|>|~', get_isotope_info(n, 
      isotope_list = nubase_isotopes, list_to_search = nubase_br_list))
  decay_types[n] = decay_distr
  try:
    average_beta_decay_energy.append(get_isotope_info(n, isotope_list= RADAR_isotopes, 
            list_to_search=RADAR_energies))
  except:
    average_beta_decay_energy.append('unknown')
    print("No RADAR data for " + n)
  try:
    abundance = float(decay_distr[decay_distr.index('B-') + 1]) / 100
  except:
    abundance = 0
  beta_decay_fractions[n] = abundance  
  beta_decay_list.append(abundance)
decay_types['63Ni']

error for isotope:  25Na
error for isotope:  184Lu
error for isotope:  165Lu
error for isotope:  21C
error for isotope:  216Pa
error for isotope:  109Sn
error for isotope:  262Md
error for isotope:  161W
error for isotope:  171Dy
error for isotope:  226Pa
error for isotope:  172Os
error for isotope:  85Y
error for isotope:  274Bh
error for isotope:  226Pu
error for isotope:  91Ru
error for isotope:  285Rg
error for isotope:  77Ni
error for isotope:  116Rh
error for isotope:  146Cs
error for isotope:  234Am
error for isotope:  43Ti
error for isotope:  56Ga
error for isotope:  206Fr
error for isotope:  287Mc
error for isotope:  45Cr
error for isotope:  227Po
error for isotope:  41Ti
error for isotope:  243Cm
error for isotope:  153Tm
error for isotope:  124La
error for isotope:  229Rn
error for isotope:  222Pa
error for isotope:  160Re
error for isotope:  170Eu
error for isotope:  113I
error for isotope:  77Ga
error for isotope:  163Tm
error for isotope:  229Np
error for isotope:  231Rn


['B-', '100']

In [99]:
beta_decay_fractions['63Ni']

1.0

In [100]:
e_t_dict['Beta-decay fraction'] = beta_decay_list
e_t_dict['Average beta decay energy'] = average_beta_decay_energy
px.scatter(x = e_t_dict['Average beta decay energy'], 
y = e_t_dict['Half life (years)'], 
hover_name = e_t_dict['Isotope'],
labels = {'x': 'Average beta-decay energy (keV)',
'y': 'Half life (years)', 'color': 'Beta-decay fraction'}, log_y = True,
color = e_t_dict['Beta-decay fraction'], color_continuous_scale = 'algae',
log_x = True)

#Synthesize isotopes with daughter nuclei that also undergo low energy beta- decay. 
Long term storage as 32Si -> excite to 33Si when necessary -> further decay into 33P
-> stable 33P.

In [35]:
get_isotope_info('32Si', 'Beta-decay energy (keV)', 'Isotope', e_t_dict)

227.1872

In [39]:
get_isotope_info('32Si', 'Half life (years)', 'Isotope', e_t_dict)

157.0

In [37]:
get_isotope_info('33Si', 'Average beta decay energy', 'Isotope', e_t_dict)

5.69

In [38]:
get_isotope_info('33Si', 'Half life (years)', 'Isotope', e_t_dict)

1.958323826906989e-07

In [40]:
get_isotope_info('33P', 'Half life (years)', 'Isotope', e_t_dict)

0.06940451745379878

In [41]:
get_isotope_info('33P', 'Average beta decay energy', 'Isotope', e_t_dict)

76.4

In [ ]:
def convert_t_s(t):
    try: 
        return (t * units.year).to(units.s) / units.s
    except:
        return 'unknown'

e_t_dict['Half life (seconds)'] = [convert_t_s(t) for t in e_t_dict['Half life (years)'] ]
power_density_of_isotope('63Ni', e_t_dict, 'Half life (seconds)', 'Beta-decay energy (keV)')

<Quantity 0.01113156>

In [66]:
no_energy = [row for row, energy in enumerate(e_t_dict['Average beta decay energy']) if (energy == 'unknown' or energy == '*')]
no_half_life = [row for row, half_life in enumerate(e_t_dict['Half life (years)']) 
               if type(half_life) is str]
not_measured_rows = no_energy + no_half_life
len(not_measured_rows)
e_t_dataframe = pd.DataFrame(e_t_dict)
filtered_e_t_df = e_t_dataframe.drop(not_measured_rows, inplace = False)
filtered_e_t_df.to_csv('NuclideData.csv')

#Evaluation of Prospective Isotopes for batteries
We first define the following
*   If $a > b$, then $max(a,b) = a$ and $min(a,b) = b$. 
*   $\rho_{p}$ is the energy in watts produced by 1g of the nuclide after 1 half life
*   $t_{\frac{1}{2}}$ is the half life in years
*   $f$ is the fraction of decays that are $\beta_{-}$ decay (one neutron emitting a W$^{-}$ boson which then decays to an up quark, an electron, and an electron neutrino). Future analysis will simulate only the electron spectra to better characterize the power produced by the battery. 

We define
\begin{equation}
\begin{split}
E = max(0, \cdot(t_{\frac{1}{2}}\rho_{p}min(t_{\frac{1}{2}}, \rho_{p}))^{3}f^{100})\\
\end{split}
\end{equation}
where a higher value for $E$ is used to distinguish which isotopes would make ideal batteries, and values of 0 are incredibly dangerous, produce insufficient power, and/or decay too quickly. Isotopes with a half life less than one year were not considered. 




In [ ]:
power_densities = [float(power_density_of_isotope(n, e_t_dict, 'Half life (seconds)',
                     'Average beta decay energy')) 
                    if not row in not_measured_rows else 'unknown' 
                    for row, n in enumerate(intersection) ]
e_t_dict['Power density (W/g)'] = power_densities
def evaluate_isotope(half_life, power_density, beta_decay_fraction):
    if(beta_decay_fraction > 0):
        beta_decay_fraction = beta_decay_fraction ** 100
    evaluation = 0
    try: 
        half_life = min(half_life ** 2, 10**4)
        coeff = min(half_life, power_density) ** 3
        if coeff > 0:
            evaluation = max(0,
            (coeff * half_life * power_density * beta_decay_fraction))
    except: 
        return 0
    return evaluation
eval_dict = {}
e_t_dict['Evaluation'] = [evaluate_isotope(t, p, f) 
                        for t, p, f in zip(e_t_dict['Half life (years)'],
                        e_t_dict['Power density (W/g)'], e_t_dict['Beta-decay fraction'])]
eval_dict = {}
for row, n in enumerate(intersection):
    eval_dict[n] = evaluate_isotope(e_t_dict['Half life (years)'][row], 
                                    e_t_dict['Power density (W/g)'][row],
                                    beta_decay_fractions[n])
e_t_dict['Half life (log(years))'] = [np.log(t) if (not type(t) is str and t > 0 ) 
                                        else 0 for t in e_t_dict['Half life (years)']]
                            

In [ ]:
power_density_df = pd.DataFrame(e_t_dict)
power_density_df.to_csv('power_density_df.csv')


In [ ]:
px.scatter(power_density_df, y = 'Power density (W/g)', x = 'Half life (years)', hover_name = 'Isotope',
             log_y = True, log_x = True,
             color = 'Beta-decay fraction', color_continuous_scale = 'algae')  

In [ ]:
measured_rows = [row for row in range(power_density_df.shape[0])
                if (not type(power_density_df['Power density (W/g)'][row]) is str) and (
                    not type(power_density_df['Half life (years)'][row]) is str)]
known_half_lives = np.array(power_density_df['Half life (years)'])[measured_rows].astype(float)
known_power_densities = np.array(power_density_df['Power density (W/g)'])[measured_rows].astype(float) 
corresponding_isotopes = np.array(power_density_df['Isotope'])[measured_rows]
#make a linear fit of the above data
m, b = np.polyfit(known_half_lives, known_power_densities, 1)
m, b

(-0.00041262712278302023, 32029982.57660088)

In [ ]:
residuals = (known_power_densities - (m * known_half_lives + b)) / known_power_densities

<ipython-input-1047-1d33a48b41ba>:1: RuntimeWarning:

divide by zero encountered in true_divide



In [ ]:
power_density_residuals_dict = {}
power_density_residuals_dict['Isotope'] = corresponding_isotopes
power_density_residuals_dict['Residuals (W/g)'] = residuals
power_density_residuals_dict['Power density (W/g)'] = known_power_densities
power_density_residuals_dict['Half life (years)'] = known_half_lives
power_density_residuals_dict['Half life (log(years))'] = np.log(known_half_lives)
power_density_residuals_df = pd.DataFrame(power_density_residuals_dict)
power_density_residuals_df.to_csv('power_density_residuals.csv')


In [ ]:
px.scatter(power_density_residuals_df, x = 'Half life (years)', y = 'Residuals (W/g)', 
    color = 'Power density (W/g)', color_continuous_scale = 'algae', log_x = True,
    hover_name='Isotope')

In [ ]:
px.scatter(power_density_residuals_df, x = 'Power density (W/g)', y = 'Residuals (W/g)', 
    hover_name='Isotope', log_x = True, log_y = True, color = 'Half life (log(years))',
    color_continuous_scale = 'algae')

In [ ]:
px.scatter(power_density_df, x = 'Power density (W/g)', y = 'Half life (years)', hover_name = 'Isotope',
             log_y = True, log_x = True,
             color = 'Beta-decay fraction', color_continuous_scale = 'algae')  

In [ ]:
px.scatter(power_density_df, x = 'Power density (W/g)', y = 'Half life (years)', hover_name = 'Isotope',
             log_y = True, log_x = True,
             color = 'Evaluation', color_continuous_scale = 'algae')  

In [ ]:
px.scatter(power_density_df, x = 'Power density (W/g)', y = 'Half life (years)', hover_name = 'Isotope',
             log_y = True, log_x = True,
             color = 'Beta-decay fraction', color_continuous_scale = 'algae')  

In [ ]:
px.scatter(power_density_df, x = 'Power density (W/g)', y = 'Half life (years)', hover_name = 'Isotope',
             log_y = True, log_x = True,
             color = 'Beta-decay fraction', color_continuous_scale = 'algae', range_y = [0.1, 100],
             range_x = [.01, 1])  

In [ ]:
px.scatter(power_density_df, x = 'Power density (W/g)', y = 'Half life (log(years))',
color = 'Evaluation', hover_name = 'Isotope', log_x = True,
color_continuous_scale = 'algae')  

In [ ]:
px.scatter(power_density_df, y = 'Evaluation', x = 'Power density (W/g)', hover_name = 'Isotope', 
            color = e_t_dict['Half life (log(years))'], color_continuous_scale = 'algae',
            log_x = True, log_y = True)

In [ ]:
px.scatter(power_density_df, y = 'Evaluation', x = 'Half life (years)', hover_name = 'Isotope',
            color_continuous_scale = 'algae', log_y= True, range_y = [10**-8,10], range_x = [10, 10**3])

In [ ]:
eval_dict = ['46Sc']

In [ ]:
eval_dict['63Ni']

7.034255676304604e-07

In [ ]:
filtered_power_density = power_density_df[(power_density_df['Evaluation'] > 10**-10) & 
                                          (type(power_density_df['Half life (years)']) is not str)]
filtered_power_density.to_csv('filtered_power_density.csv')

#Power Density Rankings
https://docs.google.com/spreadsheets/d/1GGqAvGFp6wArIsmpjYeX3BQz-2MDoCxD5flOnc9EAao/edit?usp=sharing 

In [ ]:

month_half_life = filtered_power_density[filtered_power_density['Half life (years)'] > 1/12] 
month_half_life = month_half_life.sort_values(by = 'Power density (W/g)', ascending = False)
potential_isotopes = month_half_life['Isotope'].unique()
month_half_life.set_index('Isotope', inplace = True)
month_half_life.to_csv('month_half_life.csv')
month_half_life

Beta-decay energy (keV) Half life (years)  Beta-decay fraction  \
Isotope                                                                  
89Sr                    1502.18          0.138434              1.00000   
46Sc                    2366.63          0.229314              1.00000   
141Ce                   583.476         0.0889938              1.00000   
95Zr                    1126.33           0.17531              1.00000   
35S                     167.322          0.239206              1.00000   
181Hf                   1036.11          0.116057              1.00000   
170Tm                   968.615          0.352088              0.99869   
95Nb                    925.601         0.0958001              1.00000   
45Ca                    260.091          0.445202              1.00000   
59Fe                    1564.88          0.121834              1.00000   
103Ru                   764.538          0.107447              1.00000   
160Tb                   1835.95          0.197947              1.00000   
185W                    431.176          0.205613              1.00000   
203Hg                   492.106          0.127611              1.00000   
123Sn                   1408.21           0.35373              1.00000   
192Ir                   1452.89          0.202108              0.95240   
144Ce                   318.646          0.779975              1.00000   
188W                        349           0.19102              1.00000   
204Tl                   763.745             3.783              0.97080   
60Co                    2822.81            5.2714              1.00000   
147Pm                   224.064            2.6234              1.00000   
3H                       18.592             12.32              1.00000   
124Sb                   2905.07          0.164819              1.00000   
249Bk                     123.6          0.895825              1.00000   
91Y                     1544.27          0.160192              1.00000   
182Ta                   1815.46          0.314141              1.00000   
106Ru                   39.4038           1.01793              1.00000   
90Sr                    545.967             28.91              1.00000   
125Sb                     766.7            2.7576              1.00000   
137Cs                   1175.63             30.04              1.00000   
155Eu                   251.961             4.742              1.00000   
154Eu                   1967.99             8.592              0.99982   
171Tm                   96.5468              1.92              1.00000   
39Ar                        565               268              1.00000   
32Si                    227.187               157              1.00000   
134Cs                   2058.84             2.065              1.00000   
194Os                      96.6                 6              1.00000   
63Ni                    66.9768             101.2              1.00000   
228Ra                   45.5402              5.75              1.00000   
85Kr                        687            10.728              1.00000   
241Pu                   20.7799            14.329              1.00000   
151Sm                   76.6182              94.6              1.00000   
210Pb                   63.4758              22.2              1.00000   
14C                     156.476              5700              1.00000   

        Average beta decay energy Half life (seconds) Power density (W/g)  \
Isotope                                                                     
89Sr                          189           4368643.2             16.2548   
46Sc                        111.8   7236604.800000001             11.2307   
141Ce                         130  2808432.0000000005             10.9778   
95Zr                        109.7           5532364.8             6.97957   
35S                         48.63   7548768.000000001             6.15484   
181Hf                       119.4           3662496.0           

In [ ]:
year_half_life = filtered_power_density[filtered_power_density['Half life (years)'] > 1] 
year_half_life = year_half_life.sort_values(by = 'Power density (W/g)', ascending = False)
potential_isotopes = year_half_life['Isotope'].unique()
year_half_life.set_index('Isotope', inplace = True)
year_half_life.to_csv('year_half_life.csv')
year_half_life

Beta-decay energy (keV) Half life (years)  Beta-decay fraction  \
Isotope                                                                  
204Tl                   763.745             3.783              0.97080   
60Co                    2822.81            5.2714              1.00000   
147Pm                   224.064            2.6234              1.00000   
3H                       18.592             12.32              1.00000   
106Ru                   39.4038           1.01793              1.00000   
90Sr                    545.967             28.91              1.00000   
125Sb                     766.7            2.7576              1.00000   
137Cs                   1175.63             30.04              1.00000   
155Eu                   251.961             4.742              1.00000   
154Eu                   1967.99             8.592              0.99982   
171Tm                   96.5468              1.92              1.00000   
39Ar                        565               268              1.00000   
32Si                    227.187               157              1.00000   
134Cs                   2058.84             2.065              1.00000   
194Os                      96.6                 6              1.00000   
63Ni                    66.9768             101.2              1.00000   
228Ra                   45.5402              5.75              1.00000   
85Kr                        687            10.728              1.00000   
241Pu                   20.7799            14.329              1.00000   
151Sm                   76.6182              94.6              1.00000   
210Pb                   63.4758              22.2              1.00000   
14C                     156.476              5700              1.00000   

        Average beta decay energy Half life (seconds) Power density (W/g)  \
Isotope                                                                     
204Tl                      244.03         119382400.8            0.335065   
60Co                        95.77        166352732.64            0.320852   
147Pm                       61.96         82788207.84            0.170248   
3H                           5.69         388789632.0             0.16313   
106Ru                       10.03          32123520.0           0.0984983   
90Sr                        195.8         912330216.0           0.0797398   
125Sb                        24.9         87023237.76           0.0765439   
137Cs                      174.32         947990304.0           0.0448828   
155Eu                        27.8         149646139.2           0.0400778   
154Eu                        34.5         271142899.2           0.0276285   
171Tm                         7.5          60590592.0           0.0242056   
39Ar                        218.8        8457436800.0            0.022182   
32Si                         68.8        4954543200.0           0.0145108   
134Cs                        3.55          65166444.0           0.0135943   
194Os                         3.6         189345600.0           0.0032772   
63Ni                       17.425        3193629120.0          0.00289604   
228Ra                        3.21         181456200.0          0.00259451   
85Kr                          1.5         338549932.8          0.00174304   
241Pu                        5.23  452188850.40000004           0.0016048   
151Sm                       13.96        2985348960.0          0.00103555   
210Pb                        4.16         700578720.0         0.000945527   
14C                         49.47      179878320000.0         0.000656897   

           Evaluation  Half life (log(years))  
Isotope                                        
204Tl    9.314670e-03                1.330517  
60Co     2.944911e-01                1.662296  
147Pm    5.781739e-03                0.964471  
3H       1.074865e-01                2.511224  
106Ru    9.753334e-05                0.017774  
90Sr     3.379058e-02                3.364188 

In [ ]:


decade_half_life = filtered_power_density[filtered_power_density['Half life (years)'] > 10] 
decade_half_life = decade_half_life.sort_values(by = 'Power density (W/g)', ascending = False)
potential_isotopes = decade_half_life['Isotope'].unique()
decade_half_life.set_index('Isotope', inplace = True)
decade_half_life.to_csv('decade_half_life.csv')
decade_half_life

Beta-decay energy (keV) Half life (years)  Beta-decay fraction  \
Isotope                                                                  
3H                       18.592             12.32                  1.0   
90Sr                    545.967             28.91                  1.0   
137Cs                   1175.63             30.04                  1.0   
39Ar                        565               268                  1.0   
32Si                    227.187               157                  1.0   
63Ni                    66.9768             101.2                  1.0   
85Kr                        687            10.728                  1.0   
241Pu                   20.7799            14.329                  1.0   
151Sm                   76.6182              94.6                  1.0   
210Pb                   63.4758              22.2                  1.0   
14C                     156.476              5700                  1.0   

        Average beta decay energy Half life (seconds) Power density (W/g)  \
Isotope                                                                     
3H                           5.69         388789632.0             0.16313   
90Sr                        195.8         912330216.0           0.0797398   
137Cs                      174.32         947990304.0           0.0448828   
39Ar                        218.8        8457436800.0            0.022182   
32Si                         68.8        4954543200.0           0.0145108   
63Ni                       17.425        3193629120.0          0.00289604   
85Kr                          1.5         338549932.8          0.00174304   
241Pu                        5.23  452188850.40000004           0.0016048   
151Sm                       13.96        2985348960.0          0.00103555   
210Pb                        4.16         700578720.0         0.000945527   
14C                         49.47      179878320000.0         0.000656897   

           Evaluation  Half life (log(years))  
Isotope                                        
3H       1.074865e-01                2.511224  
90Sr     3.379058e-02                3.364188  
137Cs    3.661996e-03                3.402530  
39Ar     2.421043e-03                5.590987  
32Si     4.433699e-04                5.056246  
63Ni     7.034256e-07                4.617099  
85Kr     1.062339e-09                2.372857  
241Pu    1.361815e-09                2.662285  
151Sm    1.029112e-08                4.549657  
210Pb    3.939139e-10                3.100092  
14C      1.862044e-09                8.648221

In [ ]:
century_half_life = filtered_power_density[filtered_power_density['Half life (years)'] > 100] 
century_half_life = century_half_life.sort_values(by = 'Power density (W/g)', ascending = False)
potential_isotopes = century_half_life['Isotope'].unique()
century_half_life.set_index('Isotope', inplace = True)
century_half_life.to_csv('century_half_life.csv')
century_half_life

Beta-decay energy (keV) Half life (years)  Beta-decay fraction  \
Isotope                                                                  
39Ar                        565               268                  1.0   
32Si                    227.187               157                  1.0   
63Ni                    66.9768             101.2                  1.0   
14C                     156.476              5700                  1.0   

        Average beta decay energy Half life (seconds) Power density (W/g)  \
Isotope                                                                     
39Ar                        218.8        8457436800.0            0.022182   
32Si                         68.8        4954543200.0           0.0145108   
63Ni                       17.425        3193629120.0          0.00289604   
14C                         49.47      179878320000.0         0.000656897   

           Evaluation  Half life (log(years))  
Isotope                                        
39Ar     2.421043e-03                5.590987  
32Si     4.433699e-04                5.056246  
63Ni     7.034256e-07                4.617099  
14C      1.862044e-09                8.648221

#Background physics 
For the nuclear reaction 
x + X $\to$ y + Y
we define the Q as the energy from \
mass loss:
\begin{equation}
Q = [x_{mass}+X_{mass}-y_{mass}-Y_{mass}]c^2
\end{equation}
For $\beta^-$ decay we have 
\begin{equation}
\begin{split}
n\to p + e^{-} + \bar{v}\\
Q = (n_{mass} - p_{mass} - e^{-}_{mass} - \bar{v}_{mass})c^2\\
Q = .782MeV - \bar{v}_{mass}c^2
\end{split}
\end{equation}
Assuming a massless neutrino this simplifies to .782 MeV

In [ ]:
#half_life_to_energy(.987 * 3.1536 * (10 ** 9), 1, 10**-6)[0]
avg_energy_per_decay = 17 * units.keV
mass_predecay = constants.m_n
mass_postdecay = constants.m_p + constants.m_e
Ni63_half_life = 1.02 * 3.1536 * (10 ** 9) * units.s 
time = 1 * units.s
initial_mass = (10 ** -6) * units.kg
recalc_energy_per_decay = (mass_predecay - mass_postdecay) * (constants.c ** 2)
recalc_energy_per_decay.to(units.keV) / avg_energy_per_decay

<Quantity 46.01961235>

#Potential Supply Chain
https://drive.google.com/file/d/1Mhe_WbmmahkeAE_JPnbYRvphh6IAWPwn/view?usp=sharing 

This is very similar to how neutrons are currently produced in particle 
accelerators :)


https://drive.google.com/file/d/1wPwC2eu6CqND1JRK_Dgwao7nJKzyh7Xj/view?usp=sharing 

https://drive.google.com/file/d/1t76jd7mjup9C_4SqJ5opnoNNZjVcNmSs/view?usp=sharing

Thermal neutrons (0.025 eV) are sufficient ([neutron temperature](https://https://en.wikipedia.org/wiki/Neutron_temperature), [Bryskin et al. 2004. Figure 4.](https://www.zotero.org/groups/4549380/batteries/collections/CYLBRLVK/items/T7U9LM8V/collection)) 

In [ ]:
class ni63_setup:
  '''
  This will call helper classes depending on the different steps using in the 
  production
  '''
  
  def __init__(self, **kwargs):
    self.assign_attributes(**kwargs)
    self.solar_panel_dict = {}

  def assign_attributes(self, **kwargs):
      for key in kwargs:
          setattr(self, key, kwargs[key])


In [ ]:
class solar_panel:
  '''
  Use to create a solar_panel object with a given efficiency, area, and solar flux
  ''' 
  def __init__(self, **kwargs):
    self.assign_attributes(**kwargs)

  def assign_attributes(self, **kwargs):
      for key in kwargs:
          setattr(self, key, kwargs[key])

  def calc_voltage(self):
    '''
    By definition
    power = solar_flux * efficiency * area
    power = voltage * current
    Taking the equivalent resistance of the entire circuit, we have
    voltage = current * resistance
    current = voltage / resistance
    power = voltage^2 / resistance
    voltage = sqrt(power * resistance)
    voltage = sqrt(solar_flux * efficiency * area * resistance)
    ''' 
    voltage =  np.sqrt(self.solar_flux * self.solar_panel_efficiency * 
                         self.solar_panel_area * self.resistance)
    self.voltage = voltage.to(V)

  def calc_charge_plane(self):
  #Modify appropriately for the shape of the capacitor
    self.charge = self.capacitance * self.voltage

  def calc_gamma_ray_flux(self):
    self.gamma_ray_flux = ((self.charge**2) * (self.charge_e_distance**-4) * 
                           self.brehm_coeff * self.cathode_ray_flux)

  def calc_ni63_production_speed(self):
    self.ni63_production_speed = (self.gamma_ray_flux * self.donor_cross_section
                                  * self.target_cross_section)

In [ ]:
def calc_brehm_coeff():
  echarge = 1.6021766 * (10 ** -19) * C
  return ((echarge**4) / (96 * ((math.pi * c * 8.8541878128 * (10**-12) * F / m)**3) * 
                    (m_e ** 2)))

def calc_cathode_ray_flux():
  return

In [ ]:
'''
https://www.thermofisher.com/order/catalog/product/1517021A 

50 W is sufficient for 10^8 n/s
'''

'\nhttps://www.thermofisher.com/order/catalog/product/1517021A \n\n50 W is sufficient for 10^8 n/s\n'

#Order of Magnitude of time and land area needed

##Theoretical Maximum Production per m$^2$ solar panel

With a power input of $P$ and a $E_{\gamma}$ joules for each gamma ray, assuming
each gamma ray has a $\rho$ probability of producing $^{63}$Ni we have 
\begin{equation}
\begin{split}
N = \frac{P\rho}{E_{\gamma}}\\
\end{split}
\end{equation}

In [ ]:
def g_per_year(solar_flux, area, efficiency, energy_per_neutron, molar_mass):
  power = solar_flux * area * efficiency
  nGamma = power / energy_per_neutron
  isotopes_per_second = nGamma.to(units.s ** -1) 
  molPerS = (isotopes_per_second / (constants.N_A)).to(units.mol * units.s ** -1)
  return (molPerS * (molar_mass)).to(units.g * units.year ** -1)

solar_flux = 1000 * units.W / (units.m ** 2)
area = 1 * units.m ** 2
efficiency = 1 #any real world factors that affect the production rate
energy_per_neutron = .075 * units.MeV
molar_mass = 63 * units.g / units.mol
rate = g_per_year(solar_flux, area, efficiency, energy_per_neutron, molar_mass)
rate

<Quantity 274.74003993 g / yr>

##It will take 5,000 years/m$^2$ to make enough for a car to work for 50 years.
We have a theoretical maximum of $10^{-6}$ mol nickel-63 per second for every square meter of sunlight collected per second = 36 moles per year > 2kg. Every car will need 5 years. We need 400 million m$^2$

In [ ]:
earth_rad = 6400 * units.km
earth_surface_area = np.pi * 4 * (earth_rad ** 2)
panels_area = 400 * (10**6) * (units.m ** 2)
panels_area.to(units.km ** 2) / earth_surface_area

<Quantity 7.77123746e-07>

##We need to cover 1-millionth of the Earth in solar panels. More realistically, 400 mi$^2$

##Caltech People who have done photoneutron work
*   S.R. Golwala
*   T. Aralis


##What is the energy per gamma ray and probability of Ni63 production needed to make this technology competiting in the long term compared to current forms of energy storage?

The emission of radiation by accelerating charges is derived in Chapter 14 and 
15 of the 2nd edition of Jackson's E&M. 

In [ ]:
'''
Source: 
https://www.iea.org/reports/key-world-energy-statistics-2021/final-consumption 
'''
annual_global_energy_consumed = (450 * units.EJ).to(units.W * units.year)
global_power_consumed = annual_global_energy_consumed / (1 * units.year)
efficiency = .2
power_per_area = 500 * units.W / (units.m ** 2) * efficiency
area_needed = (global_power_consumed / power_per_area).to(units.km ** 2)
area_needed

<Quantity 142596.39516313 km2>

In [ ]:
global_power_consumed / power_Si_31_per_gram

<Quantity 1.88684585e+09>

In [ ]:
global_power_consumed

<Quantity 1.42596395e+13 W>

In [ ]:
area_California_state = 423970.694 * (units.km**2)
area_California_state / area_needed

<Quantity 2.97322168>

##If we cover 1/3 of California in solar panels, we could power the world. 

##We need to cover half a million square miles with solar panels and rapidly replant native flora.

In [ ]:
#https://doi.org/10.1103/PhysRevX.7.041003
input = 40 * units.PW
Egamma= 2 * units.MeV
max_photon_flux = (input/Egamma).to(units.s ** -1)
max_photon_flux

<Quantity 1.24830181e+29 1 / s>

##Rewrite clas to be based on generating the right energy neutrons for Ni63 production.

In [ ]:
frequency = ((2 * units.MeV).to(units.J) / constants.h).to(units.Hz)
frequency 

<Quantity 4.83597848e+20 Hz>

A system that can convert between different isotopes depending on the power demand would be ideal. 


*   Requires a fast, compact, and energy efficient way to convert between emitted electrons and neutrons. 

Possibilities include using the Brehmsstrahlung effect to create gamma rays which can then be used to generate photoneutrons. This seems like the crux of 
the system.

*  



In [ ]:
def total_brehmsstrahlung_power(velocity, charge, acceleration):
  '''
  Source: 
  https://en.wikipedia.org/wiki/Bremsstrahlung#Total_radiated_power 
  '''
  beta = velocity / constants.c
  gamma = (1 - (beta ** 2)) ** -.5
  beta_dot = (acceleration / constants.c) 
  beta_term = (beta_dot ** 2) + ((beta * beta_dot) ** 2)/(1 - (beta ** 2)) 
  power = (charge ** 2) * (gamma ** 4) * beta_term / (6 * 
                  float(sym.N(sym.pi)) * constants.eps0 * constants.c)
  return power.to(units.W)

In [ ]:
total_brehmsstrahlung_power(.0000001 * constants.c, 1 * constants.e.si, .0000001 * 
                          constants.c / units.s)

<Quantity 5.13038824e-51 W>

##Using the technology of the Andasol Solar Power Station, an area half the size of Pennsylvania could power the entire world. 

In [ ]:
#https://en.wikipedia.org/wiki/Andasol_Solar_Power_Station
andasol = 2000 * units.kW * units.hour / ((units.m ** 2 ) * units.year)
andasol_efficiency = andasol.to(units.W / (units.m ** 2))
andasol_efficiency

<Quantity 228.15423226 W / m2>

In [ ]:
needed_area = (global_power_consumed / andasol_efficiency).to(units.km ** 2)
needed_area 

<Quantity 62500. km2>

In [ ]:
pennsylvania_area = 119281.9 * (units.km ** 2)
needed_area / pennsylvania_area

<Quantity 0.52396885>

In [ ]:
neutrino_mass = (1 * units.keV / (constants.c ** 2)).to(units.g)
neutrino_mass

<Quantity 1.78266192e-30 g>

#Simualted Spectrum Using the Fermi Distribution
[Approximated Energy Spectrum](https://photos.app.goo.gl/gfHG43iBdRp8a59v9 )
\begin{equation}
\begin{split}
N(T_e) = \frac{C}{c^5}(Q - T_e)^2(T + m_ec^2)\sqrt{T_e^2 + 2T_em_ec^2}\\
\end{split}
\end{equation}
Integrating this from 0 to Q and then normalizing the distribution
\begin{equation}
\begin{split}
\int_0^{T_{e \ max}} N(T_e)dT_e\\
\int_0^{T_{e \ max}} \frac{C}{c^5}(Q - T_e)^2(T_e + m_ec^2)\sqrt{T_e^2 + 2T_em_ec^2} dT_e = 1\\
C = \frac{c^5}{\int_0^{Q} (Q - x)^2(x + a)\sqrt{x^2 + 2a} dx}\\
\end{split}
\end{equation}
For some reason, [WolframAlpha](https://www.wolframalpha.com/input?i=%5Cint_0%5E%7BQ%7D+%28Q+-+x%29%5E2%28x+%2B+a%29%5Csqrt%7Bx%5E2+%2B+2a%7D+dx)
won't evaluate the integral. So using sympy, where Q = .782 MeV, a = m$_e$c$^2$,
and $x = T_e$
All units are in kg-m-s SI.

In [ ]:
Q_fermi_distr = float((.782 * units.MeV).to(units.J) / units.J)
Q_fermi_distr

1.252902127788e-13

In [ ]:

'''
We need to account for the fact that not all of the electrons will have the 
maximum energy (Q value)!
stuck for right now. Use
https://github.com/MarcosP7635/Computing-and-Formatting/blob/main/error_propagation.py
as a sympy reference
They average out to 17 keV. Rewrite to draw from a database of beta emission 
spectra. 
'''

'\nWe need to account for the fact that not all of the electrons will have the \nmaximum energy (Q value)!\nstuck for right now. Use\nhttps://github.com/MarcosP7635/Computing-and-Formatting/blob/main/error_propagation.py\nas a sympy reference\nThey average out to 17 keV. Rewrite to draw from a database of beta emission \nspectra. \n'

In [ ]:
global_power_consumed

<Quantity 1.42596395e+13 W>

In [ ]:
energy_Ni_63_per_gram = (power_Ni_63_per_gram * 50 * units.year).to(units.J)
'''
The best lithium-ion batteries store less than 1 kJ/g
Source: https://doi.org/10.1039/D0EE02681F 
'''
energy_Ni_63_per_gram 

<Quantity 17498311.8852072 J>

In [ ]:
'''
if google drive won't mount to the colab session, then
you need to download this current python notebook and upload
it to the colab session, then right click on it to copy the
path for the command below.
'''
!jupyter nbconvert --to LaTeX Energy.ipynb
#The above line makes a .tex file to format this Jupyter Notebook

[NbConvertApp] Converting notebook Energy.ipynb to LaTeX
C:\Users\engin\anaconda3\lib\site-packages\nbconvert\filters\datatypefilter.py:39: UserWarning: Your element with mimetype(s) dict_keys(['application/vnd.plotly.v1+json']) is not able to be represented.
  warn("Your element with mimetype(s) {mimetypes}"
[NbConvertApp] Writing 135492 bytes to Energy.tex
